In [ ]:
%load_ext google.colab.data_table

In [ ]:
project_id = 'dataminingproject-364904'

In [ ]:
!gcloud config list

[component_manager]
disable_update_check = True
[compute]
gce_metadata_read_timeout_sec = 0

Your active configuration is: [default]


In [ ]:
!gcloud config list project

[core]
project (unset)

Your active configuration is: [default]


In [ ]:
!gcloud config set project 'dataminingproject-364904'

Updated property [core/project].


In [ ]:
!gcloud config list project

[core]
project = dataminingproject-364904

Your active configuration is: [default]


In [ ]:
import pandas as pd
from google.colab import auth
auth.authenticate_user()
print('Authenticated')

Authenticated


In [ ]:
from google.cloud import bigquery

# https://cloud.google.com/resource-manager/docs/creating-managing-projects
client = bigquery.Client(project=project_id)

#Print your current data
for dataset in client.list_datasets():
  print(dataset.dataset_id)

CrimeCA
zillow_property_value


In [ ]:
import pandas as pd
from matplotlib import pyplot as plt # for plots
from google.colab import files # to download

In [ ]:
sql = """
SELECT
    RegionID,SizeRank,RegionName,RegionType,StateName,State,Metro,_2022_08_31,_2022_09_30,_2022_10_31
FROM
    `dataminingproject-364904.zillow_property_value.ZillowRent`
"""
dfquery = client.query(sql)

In [ ]:
df=dfquery.to_dataframe()
len(df.index)

924

In [ ]:
df=dfquery.to_dataframe()
df_aug=df.copy()
df_sep=df.copy()
df_oct=df.copy()
df_aug=df_aug[['RegionID','SizeRank','RegionName','RegionType','StateName','State','Metro','_2022_08_31']]
df_sep=df_sep[['RegionID','SizeRank','RegionName','RegionType','StateName','State','Metro','_2022_09_30']]
df_oct=df_oct[['RegionID','SizeRank','RegionName','RegionType','StateName','State','Metro','_2022_10_31']]
df_aug['month']='2022-08-31'
df_aug.rename({'_2022_08_31': 'rent'}, axis=1, inplace=True)
df_sep['month']='2022-09-30'
df_sep.rename({'_2022_09_30': 'rent'}, axis=1, inplace=True)
df_oct['month']='2022-10-31'
df_oct.rename({'_2022_10_31': 'rent'}, axis=1, inplace=True)
dfs=[df_aug,df_sep,df_oct]
df_final=pd.concat(dfs)
df_final

RegionID  SizeRank             RegionName RegionType StateName State  \
0        3101         0     Los Angeles County     county        CA    CA   
1         139         1            Cook County     county        IL    IL   
2        1090         2          Harris County     county        TX    TX   
3        2402         3        Maricopa County     county        AZ    AZ   
4        2841         4       San Diego County     county        CA    CA   
..        ...       ...                    ...        ...       ...   ...   
919      3201      1931    Westmoreland County     county        VA    VA   
920      3291      1950  Colonial Heights City     county        VA    VA   
921       777      2072           Union County     county        SD    SD   
922       528      2075           Grand County     county        CO    CO   
923      2427      2208        McKenzie County     county        ND    ND   

                                    Metro         rent       month  
0      Los Angeles-Long Beach-Anaheim, CA  2888.971871  2022-08-31  
1      Chicago-Naperville-Elgin, IL-IN-WI  1889.705163  2022-08-31  
2    Houston-The Woodlands-Sugar Land, TX  1600.312625  2022-08-31  
3               Phoenix-Mesa-Chandler, AZ  1952.230192  2022-08-31  
4      San Diego-Chula Vista-Carlsbad, CA  3101.297584  2022-08-31  
..                                    ...          ...         ...  
919                                  None  1700.000000  2022-10-31  
920                          Richmond, VA  1247.500000  2022-10-31  
921                  Sioux City, IA-NE-SD  1507.000000  2022-10-31  
922                                  None  2450.000000  2022-10-31  
923                                  None  1151.000000  2022-10-31  

[2772 rows x 9 columns]

## get counties

In [ ]:
county_sql = """
SELECT 
  c.county_name, 
  s.state as State,
  s.state_fips_code,
  c.county_fips_code,
 c.int_point_lat, c.int_point_lon
FROM `bigquery-public-data.geo_us_boundaries.counties` c, `bigquery-public-data.geo_us_boundaries.states` s
WHERE s.state_fips_code=c.state_fips_code
GROUP BY c.county_name, 
  s.state,
 c.int_point_lat, c.int_point_lon,s.state_fips_code,c.county_fips_code
"""
county_df_query = client.query(county_sql)
county_df=county_df_query.to_dataframe()
def addCounty(x):
  return x['county_name']+' County'
def processCounty(x):
  return str(x['int_point_lat'])+', '+str(x['int_point_lon'])
county_df['county_name']=county_df.apply(lambda x:addCounty(x),axis=1);
county_df['location']=county_df.apply(lambda x:processCounty(x),axis=1);
county_df.rename(columns={'county_name': 'County',"int_point_lat":'latitude','int_point_lon':'longitude'}, inplace=True)
#county_df=county_df.drop(['int_point_lat','int_point_lon'],axis=1)
county_df

County State state_fips_code county_fips_code   latitude  \
0        Bullock County    AL              01            01011  32.101759   
1         Clarke County    AL              01            01025  31.685521   
2           Clay County    AL              01            01027  33.270400   
3       Cleburne County    AL              01            01029  33.671964   
4       Randolph County    AL              01            01111  33.296475   
...                 ...   ...             ...              ...        ...   
3228     Guánica County    PR              72            72055  17.948052   
3229    Peñuelas County    PR              72            72111  18.026618   
3230    St. John County    VI              78            78020  18.330435   
3231   St. Croix County    VI              78            78010  17.735321   
3232  St. Thomas County    VI              78            78030  18.326748   

      longitude                 location  
0    -85.717261  32.1017589, -85.7172613  
1    -87.818624  31.6855211, -87.8186244  
2    -85.863525  33.2703999, -85.8635254  
3    -85.516126  33.6719637, -85.5161261  
4    -85.464068  33.2964753, -85.4640679  
...         ...                      ...  
3228 -66.922989  17.9480521, -66.9229889  
3229 -66.728125  18.0266179, -66.7281249  
3230 -64.735261   18.3304347, -64.735261  
3231 -64.746741  17.7353214, -64.7467405  
3232 -64.971251   18.326748, -64.9712508  

[3233 rows x 7 columns]

In [ ]:
county_df = county_df.drop_duplicates()
len(county_df.index)

3233

In [ ]:
df_temp=county_df[county_df['County']=="Orange County"]
df_temp

County State state_fips_code county_fips_code   latitude  \
207   Orange County    CA              06            06059  33.675687   
365   Orange County    FL              12            12095  28.514391   
700   Orange County    IN              18            18117  38.547381   
1876  Orange County    NY              36            36071  41.402410   
1933  Orange County    NC              37            37135  36.062525   
2665  Orange County    TX              48            48361  30.122323   
2818  Orange County    VT              50            50017  44.003392   
2837  Orange County    VA              51            51137  38.250193   

       longitude                  location  
207  -117.777207  33.6756872, -117.7772068  
365   -81.323284   28.5143906, -81.3232839  
700   -86.489257    38.5473812, -86.489257  
1876  -74.306252   41.4024096, -74.3062522  
1933  -79.120034    36.0625255, -79.120034  
2665  -93.894100   30.1223229, -93.8940999  
2818  -72.369687   44.0033924, -72.3696871  
2837  -78.009622    38.250193, -78.0096224

In [ ]:
len(df_final.index)
df_final = df_final.drop_duplicates()
len(df_final.index)

2772

In [ ]:
df_merged = pd.merge(df_final,county_df, how='inner',left_on=['RegionName','State'],right_on=['County','State'])
len(df_merged.index)

2574

In [ ]:
df_merged

RegionID  SizeRank          RegionName RegionType StateName State  \
0         3101         0  Los Angeles County     county        CA    CA   
1         3101         0  Los Angeles County     county        CA    CA   
2         3101         0  Los Angeles County     county        CA    CA   
3          139         1         Cook County     county        IL    IL   
4          139         1         Cook County     county        IL    IL   
...        ...       ...                 ...        ...       ...   ...   
2569       528      2075        Grand County     county        CO    CO   
2570       528      2075        Grand County     county        CO    CO   
2571      2427      2208     McKenzie County     county        ND    ND   
2572      2427      2208     McKenzie County     county        ND    ND   
2573      2427      2208     McKenzie County     county        ND    ND   

                                   Metro         rent       month  \
0     Los Angeles-Long Beach-Anaheim, CA  2888.971871  2022-08-31   
1     Los Angeles-Long Beach-Anaheim, CA  2902.640705  2022-09-30   
2     Los Angeles-Long Beach-Anaheim, CA  2903.093932  2022-10-31   
3     Chicago-Naperville-Elgin, IL-IN-WI  1889.705163  2022-08-31   
4     Chicago-Naperville-Elgin, IL-IN-WI  1890.373113  2022-09-30   
...                                  ...          ...         ...   
2569                                None  2315.580667  2022-09-30   
2570                                None  2450.000000  2022-10-31   
2571                                None          NaN  2022-08-31   
2572                                None          NaN  2022-09-30   
2573                                None  1151.000000  2022-10-31   

                  County state_fips_code county_fips_code   latitude  \
0     Los Angeles County              06            06037  34.196398   
1     Los Angeles County              06            06037  34.196398   
2     Los Angeles County              06            06037  34.196398   
3            Cook County              17            17031  41.894294   
4            Cook County              17            17031  41.894294   
...                  ...             ...              ...        ...   
2569        Grand County              08            08049  40.113065   
2570        Grand County              08            08049  40.113065   
2571     McKenzie County              38            38053  47.742475   
2572     McKenzie County              38            38053  47.742475   
2573     McKenzie County              38            38053  47.742475   

       longitude                  location  
0    -118.261862  34.1963983, -118.2618616  
1    -118.261862  34.1963983, -118.2618616  
2    -118.261862  34.1963983, -118.2618616  
3     -87.645455   41.8942937, -87.6454546  
4     -87.645455   41.8942937, -87.6454546  
...          ...                       ...  
2569 -106.110837  40.1130652, -106.1108366  
2570 -106.110837  40.1130652, -106.1108366  
2571 -103.403215  47.7424751, -103.4032148  
2572 -103.403215  47.7424751, -103.4032148  
2573 -103.403215  47.7424751, -103.4032148  

[2574 rows x 15 columns]

In [ ]:
output_dataset_id='zillow_property_value'

output_table_id = 'ZillowRentProcessed' 

replace_or_append_output = 'replace' #['replace', 'append']

# Combine project and dataset
project_dataset = (client.project + '.' + output_dataset_id)

# Check to make sure output dataset exists, create it if not
try:
  client.get_dataset(output_dataset_id)
  print("Dataset " + project_dataset + " exists\n")
 
except:
  print("Dataset " + project_dataset + " doesn't exist, so creating it\n")
  dataset = client.create_dataset(bigquery.Dataset(project_dataset))

Dataset dataminingproject-364904.zillow_property_value exists



In [ ]:
def createTable(df,output_table_id):
    job_config = bigquery.LoadJobConfig()

    # Modify job config depending on if we want to replace or append to table
    if(replace_or_append_output == 'replace'):
      job_config.write_disposition = bigquery.WriteDisposition.WRITE_TRUNCATE  
    else:  
      job_config.write_disposition = bigquery.WriteDisposition.WRITE_APPEND

    dataset_ref = client.dataset(output_dataset_id)
    table_ref = dataset_ref.table(output_table_id)

    # Use client functionality to load BigQuery table from Pandas data frame
    client.load_table_from_dataframe(
    dataframe = df,
    destination = table_ref,
    job_config = job_config
    ).result()
    
    print('Write to bigquery dataset (' + replace_or_append_output + ') to ' + project_dataset + '.' + output_table_id +'\n')
createTable(df_merged,output_table_id)

Write to bigquery dataset (replace) to dataminingproject-364904.zillow_property_value.ZillowRentProcessed



## Map prices to counties

In [ ]:
!pip install kaleido
!apt-get install poppler-utils 
!pip install pdf2image


Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Reading package lists... Done
Building dependency tree       
Reading state information... Done
poppler-utils is already the newest version (0.62.0-2ubuntu2.14).
The following package was automatically installed and is no longer required:
  libnvidia-common-460
Use 'apt autoremove' to remove it.
0 upgraded, 0 newly installed, 0 to remove and 5 not upgraded.
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
!pip install plotly-geo
!pip install geopandas
!pip install pyshp
!pip install shapely

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
import plotly.graph_objects as go
import plotly.express as px
import plotly.io as pio
import plotly.figure_factory as ff
pio.templates.default = "plotly_dark"
import seaborn as sns

In [ ]:
map_df=df_merged[df_merged['month']=='2022-10-31']
county_crimes = pd.DataFrame(map_df.groupby(['County','latitude','longitude'])['rent'].sum()).reset_index().sort_values(by='rent', ascending=False).reset_index(drop=True)
fig = px.density_mapbox(county_crimes, lat='latitude', lon='longitude', radius=15,
                        center=dict(lat=39.9922953, lon=-120.8243709), zoom=5, hover_name = 'rent',
                        mapbox_style='stamen-terrain')
fig.show()


In [ ]:
import numpy as np
import pandas as pd

df_sample = df_merged[df_merged['month']=='2022-10-31'].copy()
df_sample['State FIPS Code'] = df_sample['state_fips_code'].apply(lambda x: str(x).zfill(2))
df_sample['County FIPS Code'] = df_sample['county_fips_code'].apply(lambda x: str(x).zfill(3))
df_sample['FIPS'] =  df_sample['County FIPS Code']
#df_sample['State FIPS Code'] +
colorscale = ["#f7fbff","#ebf3fb","#deebf7","#d2e3f3","#c6dbef","#b3d2e9","#9ecae1",
              "#85bcdb","#6baed6","#57a0ce","#4292c6","#3082be","#2171b5","#1361a9",
              "#08519c","#0b4083","#08306b"]
endpts = list(np.linspace(1, 12, len(colorscale) - 1))
fips = df_sample['FIPS'].tolist()
values = df_sample['rent'].tolist()

fig = ff.create_choropleth(
    fips=fips, values=values,
    binning_endpoints=endpts,
    colorscale=colorscale,
    show_state_data=False,
    show_hover=True, centroid_marker={'opacity': 0},
    asp=2.9, title='USA Rents by County',
    legend_title='Rent'
)

fig.layout.template = None
fig.show()

/usr/local/lib/python3.7/dist-packages/plotly/figure_factory/_county_choropleth.py:361: ShapelyDeprecationWarning:

Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.

/usr/local/lib/python3.7/dist-packages/plotly/figure_factory/_county_choropleth.py:365: ShapelyDeprecationWarning:

Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.

/usr/local/lib/python3.7/dist-packages/plotly/figure_factory/_county_choropleth.py:368: ShapelyDeprecationWarning:

Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.

/usr/local/lib/python3.7/dist-packages/plotly/figure_factory/_county_choropleth.py:369: ShapelyDeprecationWarning:

Iteration over multi-pa

In [ ]:
topCountyrentsMax = pd.DataFrame(df_merged[df_merged['month'] == '2022-10-31'].groupby(['County'])['rent'].sum()).reset_index().sort_values(by='rent', ascending=False).reset_index(drop=True).loc[:10,'County'].values
topCountyrentsMin = pd.DataFrame(df_merged[df_merged['month'] == '2022-10-31'].groupby(['County'])['rent'].sum()).reset_index().sort_values(by='rent', ascending=True).reset_index(drop=True).loc[:10,'County'].values

In [ ]:
df_merged['processed_date']=pd.to_datetime(df_merged["month"])

In [ ]:
fig = go.Figure()
df_counts=[]
for county in topCountyrentsMax:
    info_state = pd.DataFrame(df_merged[df_merged['County'] == county].groupby('month')['rent'].sum()).reset_index().sort_values(by='month')
    df_temp=info_state.copy()
    df_temp['County']=[county for i in range(len(df_temp))]
    df_counts.append(df_temp)
    fig.add_trace(go.Scatter(x=info_state.month, y=info_state.rent, name=county))
fig.update_layout(title_text='Rent in top 10 Counties with maximum rent', title_x=0.5)

fig.show()

In [ ]:
fig = go.Figure()
df_counts=[]
for county in topCountyrentsMin:
    info_state = pd.DataFrame(df_merged[df_merged['County'] == county].groupby('month')['rent'].sum()).reset_index().sort_values(by='month')
    df_temp=info_state.copy()
    df_temp['County']=[county for i in range(len(df_temp))]
    df_counts.append(df_temp)
    fig.add_trace(go.Scatter(x=info_state.month, y=info_state.rent, name=county))
fig.update_layout(title_text='Rent in top 10 Counties with minimum rent', title_x=0.5)

fig.show()